In [19]:
import pandas as pd
from urllib import request
import folium

# Get Data

Data was referred from Data is Plural via email subscription

Data is from [NYC Parks and Recreation - Street Tree Planting Locations](https://www.nycgovparks.org/trees/street-tree-planting/locations)



In [14]:
r = request.urlopen('https://www.nycgovparks.org/tree-work-orders/street_tree_planting.csv')

last_build_date = r.readlines()[5].decode('utf-8').split(',')[1].strip('\n')
last_build_date

'"2022-08-01 00:48:56"'

In [15]:
df = pd.read_csv('https://www.nycgovparks.org/tree-work-orders/street_tree_planting.csv', skiprows=7)
df

lng        lat    Borough  ZipCode BuildingNumber  \
0    -73.709503  40.740340     Queens    11004         82-030   
1    -73.954008  40.814634  Manhattan    10027            464   
2    -73.712984  40.735428     Queens    11001         254-04   
3    -73.952187  40.799678  Manhattan    10026             37   
4    -73.876284  40.828165      Bronx    10472           1155   
...         ...        ...        ...      ...            ...   
8167 -73.955075  40.803470  Manhattan    10026            243   
8168 -73.947633  40.802097  Manhattan    10026             41   
8169 -73.947518  40.802062  Manhattan    10026             41   
8170 -73.949069  40.801668  Manhattan    10026             60   
8171 -74.018785  40.639146   Brooklyn    11220            430   

               StreetName  FiscalYear  PlantingSpaceID  CommunityBoard  \
0              260 STREET           0           148027             413   
1         WEST 129 STREET           0           156427             109   
2                 84 ROAD           0           177638             413   
3     MALCOLM X BOULEVARD           0           178031             110   
4            MANOR AVENUE           0           191641             209   
...                   ...         ...              ...             ...   
8167             W 115 ST           0          9897398             110   
8168      WEST 117 STREET           0          1575732             110   
8169     WEST 117 STREET            0          9897851             110   
8170     WEST 116 STREET            0          9897852             110   
8171                62 ST           0          9097266             307   

     PlantingSeason  CityCouncil  TreeID      WOId       WOStatus  \
0        05/31/2022           23  114029  15525248      Completed   
1        05/31/2022            7       0  16644663  Not Completed   
2        05/31/2022           23  142438   8573730      Completed   
3        05/31/2022            9  143233   9138879  Not Completed   
4        05/31/2022           18       0  14343624  Not Completed   
...             ...          ...     ...       ...            ...   
8167     05/31/2022            9       0  18573063  Not Completed   
8168     05/31/2022            9       0  18575180  Not Completed   
8169     05/31/2022            9       0  18575179  Not Completed   
8170     05/31/2022            9       0  18575178  Not Completed   
8171     05/31/2022           38       0  16284351      Completed   

            CompletedDate  
0     2021-12-07 00:00:00  
1                     NaN  
2     2021-12-07 00:00:00  
3                     NaN  
4                     NaN  
...                   ...  
8167                  NaN  
8168                  NaN  
8169                  NaN  
8170                  NaN  
8171  2022-05-19 00:00:00  

[8172 rows x 15 columns]

In [17]:
df['CompletedDate'] = pd.to_datetime(df['CompletedDate'])
df['PlantingSeason'] = pd.to_datetime(df['PlantingSeason'])

In [18]:
df['CompletedDate'].dt.year.unique()

array([2021.,   nan, 2022., 2016., 2018.])

In [30]:
nyc_map = folium.Map(location=[40.7128, -74.0060], zoom_start=12)
records = df[df['WOStatus'] == 'Completed'][['lat', 'lng', 'CompletedDate']].to_records()

for record in records:
    folium.Marker(location=[record[1], record[2]],
                  icon=folium.Icon(color='green',
                                   icon_color='white',
                                   icon='tree',
                                   prefix='fa',
                                   ),
                  # popup=record[4],
                  tooltip=f"Completed Date: {record[3]}"
                  ).add_to(nyc_map)

nyc_map

In [43]:
# Reference: https://geoffboeing.com/2015/10/exporting-python-data-geojson/
def df_to_geojson(df, properties, lat='latitude', lon='longitude'):
    geojson = {'type':'FeatureCollection', 'features':[]}
    for _, row in df.iterrows():
        feature = {'type':'Feature',
                   'properties':{},
                   'geometry':{'type':'Point',
                               'coordinates':[]}}
        feature['geometry']['coordinates'] = [row[lon],row[lat]]
        for prop in properties:
            feature['properties'][prop] = row[prop]
        geojson['features'].append(feature)
    return geojson

In [44]:
import json

geojson = df_to_geojson(df[df['WOStatus'] == 'Completed'].rename({'lat': 'latitude', 'lng': 'longitude', 'CompletedDate': 'times'}, axis=1), ['times'])

output_filename = 'dataset.js'
with open(output_filename, 'wb') as output_file:
    output_file.write('var dataset = ')
    json.dumps(geojson, output_file, indent=2)

TypeError: a bytes-like object is required, not 'str'

In [46]:
with open('dataset.geojson') as j:
    data = json.load(j)

JSONDecodeError: Expecting value: line 1 column 1 (char 0)